# Let's Evaluate Tiny MoE





### Configure the machine and install packages


In [1]:
from typing import Literal

import os

os.environ["XLA_FLAGS"] = '--xla_force_host_platform_device_count=8'

import jax

platform : Literal["darwin", "colab", "cuda", "tpu"] = "darwin"

try:
    import google.colab
    platform = "colab"
except ImportError:
    devices = jax.devices()
    if any(d.platform == "gpu" for d in devices):
        platform = "cuda"
    if any(d.platform == "tpu" for d in devices):
        platform = "tpu"

print(f"Running on {platform}")

if platform == "colab":
    !git clone https://github.com/novastar53/jaxpt
    !cd jaxpt && git checkout main && git pull
    !pip install tiktoken datasets --quiet
    !pip uninstall -y tensorflow

Running on darwin


In [2]:
from pathlib import Path
import sys

if platform == "colab":
    jaxpt_dir = str(Path().absolute() / "jaxpt" / "src" )
else:
    jaxpt_dir = str(Path().absolute().parent / "src" )


sys.path.append(jaxpt_dir)
print(jaxpt_dir)

/Users/vikram/dev/jaxpt/src


In [3]:
import os


import warnings

import jax
from jax.sharding import Mesh, PartitionSpec, NamedSharding
import flax
import jax.numpy as jnp
import numpy as np

# Hardware setup
print("JAX version:", jax.__version__)
print("Flax version", flax.__version__)

devices = jax.devices()
num_devices = len(devices)
print("Available devices:", num_devices)

requested_device = "gpu"

jax.config.update("jax_platform_name", requested_device) # Make sure we're using the GPU

device = jax.default_backend()
if device != requested_device:
    warnings.warn(f"not using {requested_device}. Using {device}")
else:
    print(f"using {device}")


#####################################
##        jax.lax matmul presets   ##
#####################################
## 'ANY_F8_ANY_F8_F32',
## 'ANY_F8_ANY_F8_F32_FAST_ACCUM'
## 'ANY_F8_ANY_F8_ANY'
## 'ANY_F8_ANY_F8_ANY_FAST_ACCUM'
## 'F16_F16_F16'
## 'F16_F16_F32'
## 'BF16_BF16_BF16'
## 'BF16_BF16_F32'
## 'BF16_BF16_F32_X3'
## 'BF16_BF16_F32_X6'
## 'TF32_TF32_F32'
## 'TF32_TF32_F32_X3'
## 'F32_F32_F32'
## 'F64_F64_F64'
#####################################

jax.config.update("jax_default_matmul_precision", "BF16_BF16_F32") # Set the default precision for matrix multiplication

#jax.config.update("jax_enable_x64", True) # Make sure the highest precision is enabled in case we need
#os.environ["NVIDIA_TF32_OVERRIDE"] = "1"
#os.environ["JAX_ENABLE_X64"] = "False"

if device == "tpu":
    def list_tpu_memory():
        devices = jax.devices()
        for device in devices:
            if 'TPU' in str(device.device_kind):
                print(f"Device: {device}, Memory: {device.memory_stats()['bytes_limit']/(1024*1024)},  Used: {device.memory_stats()['bytes_in_use']/(1024*1024)}")

    list_tpu_memory()

# Set up device mesh


mesh = jax.sharding.Mesh(jax.devices(), ["devices"])

# Test the device
A = jnp.array(np.random.normal(size=(4096, 4096)), dtype=jnp.float32) # Make sure matmul is fast
%timeit (A@A).block_until_ready()

JAX version: 0.6.2
Flax version 0.10.7
Available devices: 8


/var/folders/x4/85_9sn3d1ng9q48ff6t3fw340000gn/T/ipykernel_63122/3250393803.py:26: UserWarning: not using gpu. Using cpu
  warnings.warn(f"not using {requested_device}. Using {device}")


215 ms ± 11.8 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [26]:
from flax import nnx

from jaxpt.infer import generate_completions, generate
from jaxpt.models import Tiny_MoE_Config, Tiny_MoE
from jaxpt.utils import count_params, create_sharded_model
from jaxpt.checkpointers import load_checkpoint_from_gcloud

import tiktoken
from transformers import AutoTokenizer

key = jax.random.PRNGKey(1337)
rngs = nnx.Rngs(key)
config = Tiny_MoE_Config(dtype=jnp.bfloat16, \
                     vocab_size=49152,
                     n_layer=30,
                     block_size=2048,
                     n_head=9,
                     n_kv_head=3,
                     n_mlp_hidden=1536,
                     expert_weight_priority=False,
                     load_factor=2.0,
                     sdpa_implementation="cudnn" if device=="gpu" else "xla")
nnx.display(config)
with mesh:
    m = load_checkpoint_from_gcloud(Tiny_MoE, config, Path().absolute().parent , "alpha_training_runs", "run_20250728_mercapto_inkstand", 120000, rngs)
    #m = create_sharded_model(Tiny_MoE, config, rngs)
    #m = load_checkpoint(Tiny_MoE, output_dir, config, "run_20250716_htlpzj", 180000, rngs)
    #m = load_checkpoint(Tiny_MoE, output_dir, config, "run_20250716_htlpzj", 381469, rngs)
    #m = from_hf_pretrained(config, rngs)

    graphdef, rngstate, state = nnx.split(m, nnx.RngState, ...)
    total_params = count_params(m)
    moe_params = count_params(m, "moe")

    print(f"Parameter Count: {total_params:,}")
    print(f"MOE Parameter Count: {moe_params:,}")
    print(f"Replicated Parameter Count: {total_params - moe_params:,}")
    nnx.display(state)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
/Users/vikram/dev/jaxpt/.venv/lib/python3.12/site-packages/orbax/checkpoint/_src/serialization/type_handlers.py:1251: UserWarning: Sharding info not provided when restoring. Populating sharding info from sharding file. Please note restoration time will be slightly increased due to reading from file. Note also that this option is unsafe when restoring

Parameter Count: 413,713,728
MOE Parameter Count: 319,011,840
Replicated Parameter Count: 94,701,888


In [27]:
with mesh:
    enc = AutoTokenizer.from_pretrained("HuggingFaceTB/SmolLM-360M")
    completions = generate_completions(m, enc=enc, num_completions=8,
                                    max_length=40,
                                    key=jax.random.key(0),
                                    temperature=0.5,
                                    prefix="The first mission to Jupiter was")
    for completion in completions:
        print(completion)
        print('---------------------------')

The first mission to Jupiter was the discovery of the first Jupiter-like planet, named GJ 1151b, in 1995. The discovery of GJ 1
---------------------------
The first mission to Jupiter was the Voyager 2, which became the first spacecraft to visit the gas giant. The next mission, Voyager 3, was launched in 1980 and has
---------------------------
The first mission to Jupiter was the first to the orbit of the gas giant. The Juno mission was the first to investigate the planet’s atmosphere.
The Juno mission was the first to study the
---------------------------
The first mission to Jupiter was the Pioneer 10 mission, which was launched in 1979 and was the first direct probe to Jupiter. The Pioneer 11 mission was the first
---------------------------
The first mission to Jupiter was the New Horizons mission, which flew by Pluto in 2015.
The first spacecraft to visit Jupiter was the Galileo spacecraft, which flew by Jupiter in 
---------------------------
The first mission to Jupiter was th

## Run Hellaswag Eval 

In [ ]:
import time
from jaxpt.evals.hellaswag import HellaSwag

with mesh:
    hellaswag = HellaSwag(m)
    hellaswag.batch_size = 8

    total, correct = 0, 0
    start = time.time()
    for _example, pred, label in hellaswag:
        # print(example["ctx"])
        # for ending in example["endings"]:
        #    print(ending)
        # print(pred, label)
        # print("----------")
        # print(f"Processed: {total}", end="\r")
        total += 1
        correct += int(pred == label)

        if total % 1 == 0:
            delta = time.time() - start
            rate = total / delta
            print(
                f"correct {correct} | total {total} | acc {100 * correct / total:0.2f}% | rate {rate:0.1f}/sec "
            )

    print(f"Accuracy: {100 * correct / total}%")


ValueError: too many values to unpack (expected 3)

In [ ]:
import seaborn as sns
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt

df = pd.read_csv("../logs/Tiny_MoE_logs_run_20250722_uhixrg_train (1).csv")

# Extract iterations and loss columns (replace with actual column names if different)
iterations = df['step']
loss = df['loss']

# Set pastel style
sns.set(style="whitegrid", palette="pastel")

plt.figure(figsize=(10, 6))
sns.lineplot(x=iterations, y=loss, linewidth=2.5)
plt.title('Training Loss over Iterations', fontsize=16)
plt.xlabel('Iteration', fontsize=14)
plt.ylabel('Loss', fontsize=14)
plt.yticks(np.arange(int(loss.min()), int(loss.max()) + 1, 0.5))
plt.grid(True, which='both', linestyle='--', linewidth=0.5)
plt.tight_layout()
plt.show()